In [ ]:

def high_div(symbols):

    api_key1 = '86dd63f6b8ae774b061232685b78eb52'
    stocks = pd.DataFrame(columns = ['mktCap','price','symbol','volAvg','lastDiv'])
    #ticker = 'FAST'
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/profile/{ticker}?apikey={api_key1}').json()[0]
            stocks = stocks.append({'mktCap':bs['mktCap'],'price':bs['price'], 'symbol':bs['symbol'], 'volAvg':bs['volAvg'],'lastDiv':bs['lastDiv']}, ignore_index=True)
            stocks['dividend_yield'] = stocks['lastDiv']/stocks['price']
        except:
            pass
    stocks =stocks.set_index('symbol')
        
    
    api_key1 = '86dd63f6b8ae774b061232685b78eb52'
    stocks1 = pd.DataFrame(columns = ['dividendYielPercentageTTM','payoutRatioTTM','symbol'])
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={api_key1}').json()[0]
            stocks1 = stocks1.append({'dividendYielPercentageTTM':bs['dividendYielPercentageTTM'],'payoutRatioTTM':bs['payoutRatioTTM'], 'symbol':ticker}, ignore_index=True)
        except:
            pass
    stocks1 =stocks1.set_index('symbol')        

    ############DIVIDEND ARE BASED ON YEARLY###############
    stocks2 = pd.DataFrame(columns = [ "fiveYDividendperShareGrowthPerShare", "threeYDividendperShareGrowthPerShare"])
    
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?apikey={api_key1}').json()[0]
            stocks2 = stocks2.append({"fiveYDividendperShareGrowthPerShare":bs["fiveYDividendperShareGrowthPerShare"],"threeYDividendperShareGrowthPerShare":bs["threeYDividendperShareGrowthPerShare"], 'symbol':ticker}, ignore_index=True)
    
        except:
            pass
    stocks2 =stocks2.set_index('symbol')             
    
    stocks1 = stocks1.sort_index()
    stocks2=stocks2.sort_index()
    stocks=stocks.sort_index()
    all_data = pd.concat([stocks, stocks2,stocks1], axis=1, join="inner")
    #  all_data 
    # data=stocks.merge(stocks1, left_index=True, right_index=True)
    # all_data = data.merge(stocks2,left_index=True, right_index=True)
    
   #all_data =all_data.dropna()

    div = pd.DataFrame()
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/stock_dividend/{ticker}?apikey={api_key1}').json()['historical']
            dividend=pd.DataFrame(columns = ['date','dividend'])
            for i in range(len(bs)):
                dividend= dividend.append({'date':bs[i]['date'], 'dividend':bs[i]['dividend']}, ignore_index = True)
                
            dividend_data = pd.DataFrame(columns = ['date','dividend'])
            for i in range(1,len(dividend)):
                dividend_data =  dividend_data.append({'date':bs[i]['date'], 'dividend':bs[i]['dividend']}, ignore_index = True)
                if i >21:
                    break 
            
            
            div_data = pd.DataFrame(columns = ['date','dividendAvg'])
            for i in range(6):
                div_data=  div_data.append({'date': dividend_data['date'][ 4*i], 'dividendAvg':dividend_data['dividend'][ 4*i]},ignore_index = True)
            
            div_data ['dividendAvg'] =div_data['dividendAvg']*4
            avg_div3y = div_data.loc[1:3,'dividendAvg'].mean()
            avg_div5y =div_data.loc[1:5,'dividendAvg'].mean()
            one_yearchange = (div_data.loc[0,'dividendAvg']-div_data.loc[1,'dividendAvg'])/div_data.loc[1,'dividendAvg']
            dataa =pd.DataFrame(columns = ['symbol', 'avg_div3y','avgdiv5y', 'one_yearchange'])
            dataa = dataa.append({'symbol':ticker, 'avg_div3y':avg_div3y ,'avgdiv5y':avg_div5y,'one_yearchange':one_yearchange}, ignore_index = True)
            div =pd.concat([div,dataa], axis =0)
            
        except:
            pass
    div= div.set_index('symbol')
    #div =div.dropna()
    div = div.sort_index()
    
    all_data1 = pd.concat([ all_data ,div], axis=1, join="inner")
  #  all_data1 = all_data.merge(div,left_index=True, right_index=True)
    all_data1= all_data1.dropna()
        
    all_data1 = all_data1[all_data1['mktCap'] >2000000000]
    all_data1 =  all_data1[all_data1['dividend_yield'] >0.015]
    all_data1 =  all_data1[all_data1['one_yearchange'] >0.02]
    all_data1 =  all_data1[all_data1["avg_div3y"]>0]
    all_data1 =  all_data1[all_data1[ "avgdiv5y"]>0]
    all_data1 = all_data1[all_data1['payoutRatioTTM'] > 0.3] 
    all_data1 = all_data1[ all_data1['payoutRatioTTM'] <0.8]
    return all_data1

n =3
high_dividend =pd.DataFrame()
groups = np.array_split(symbols, n)
import time
for group in groups:
    for ticker in group:
        hig_dividend = high_div(ticker)
    high_dividend = pd.concat([high_dividend,hig_dividend],axis =0)
    time.sleep(60)
n = 3# number of groups
groups = np.array_split(symbols, n)
group1 = groups[0].tolist()
group2 = groups[1].tolist()
group3 = groups[2].tolist()
#group4 = groups[3].tolist()
#group5 = groups[4].tolist()
data1 =high_div(group1)
data2 =high_div(group2)
data3 =high_div(group3)
